In [1]:
import requests
import pandas as pd
import time
pd.set_option("display.max_columns", None)
import datetime
from datetime import timezone, timedelta
from geopy.distance import geodesic #計算GPS兩端點距離
import folium #GPS數據視覺化
from global_land_mask import globe #確認GPS位置是否在陸地
import warnings
warnings.filterwarnings('ignore') # 關閉運行的警告
pd.set_option("mode.chained_assignment", None)
import pprint
import json
import tkinter as tk
from tkinter import filedialog
import gc
import sqlite3
import httpx
import numpy as np
import os

In [18]:
res = requests.get("https://leak.gewohler.icu/db/DE6BE22CCBBA25E4F1101B941CF173BB.csv")

',,,,,,,,,,,,,,,,,formula in A,Sheet names\nKAA-0016,å¯\x8cç\x81¥é\x81\x8aè¦½è»\x8aæ\x9c\x89é\x99\x90å\x85¬å\x8f¸, , , , , , ,ISUZU,200602,4751, , , ,389-V8, , ,,KAB-3\nKAA-0017,æµ¯æ±\x9fé\x80\x9aé\x81\x8bè\x82¡ä»½æ\x9c\x89é\x99\x90å\x85¬å\x8f¸, , , , , , ,TOYOTA,199301,4164, , , , , , ,,KAB-5\nKAA-0018,ä¸\x96è±ªé\x81\x8aè¦½è»\x8aæ\x9c\x89é\x99\x90å\x85¬å\x8f¸, , , , , , ,TOYOTA,200502,4104, , , , , , ,,KAB-6\nKAA-0019,æµ¯æ±\x9fé\x80\x9aé\x81\x8bè\x82¡ä»½æ\x9c\x89é\x99\x90å\x85¬å\x8f¸, , , , , , ,ISUZU,200604,5193, , , ,268-TT, , ,,KAB-7\nKAA-0020,é\x87\x91é\x96\x80é\x9b\x84ç\x8d\x85å\x9c\x8bé\x9a\x9bé\x80\x9aé\x81\x8bè\x82¡ä»½æ\x9c\x89é\x99\x90å\x85¬å\x8f¸, , , , , , ,MITSUBISHI,200206,11945, , , , , , ,,KAB-8\nKAA-0021,æ¥\x93è\x93®é\x80\x9aé\x81\x8bè\x82¡ä»½æ\x9c\x89é\x99\x90å\x85¬å\x8f¸, , , , , , ,TOYOTA,200811,4009, , , , , , ,,KAB-9\nKAA-0022,é\x81\x8bé\x80\x9aæ\x97\x85é\x81\x8bæ\x9c\x89é\x99\x90å\x85¬å\x8f¸, , , , , , ,MITSUBISHI,200209,11945, , , , , , ,,KAC-0\nKAA-0023,é\x96©æ

In [49]:
dtime = datetime.datetime(2023, 4, 28, 11, 59)
while True:
    cur_time = datetime.datetime.now()
    if dtime <= cur_time:
        print("Now is {}".format(cur_time))
        break
    time.sleep(1)

Now is 2023-04-28 11:59:00.978042


In [7]:
start_date = datetime.date(2021, 7, 1)

In [17]:
datetime.datetime.strptime(start_date.strftime("%Y-%m-%d"), "%Y-%m-%d")

datetime.datetime(2021, 7, 1, 0, 0)

In [8]:
start_date + timedelta(days=3)

datetime.date(2021, 7, 4)

## 每次執行前先更新路線和業者資訊

In [2]:
icb_route_api = "https://linkmotc.map8.zone/app/data?modelName=route_coach&skip=0&limit=&whereOptions="
icb_operator_api = "https://linkmotc.map8.zone/app/data?modelName=operator_coach&skip=0&limit=&whereOptions="

In [3]:
def update_api(api):
    res = httpx.get(api)
    df = pd.read_json(res.text)
    return df
    

## 從TDX歷史資料匯入資料庫
### server: TDX.db
### table: ICB

In [76]:
fetch_date = pd.DataFrame(pd.date_range(start="2021-07-01", end=datetime.date.today() - timedelta(days=1), freq="D"), columns=["start_date"])

In [81]:
fetch_date["end_date"] = fetch_date["start_date"] + timedelta(days=7)

In [24]:
tdx = TDX()
base_url = "https://tdx.transportdata.tw/api/basic"
endpoint = "/v2/Road/Traffic/Live/VD/City/Taipei"
query = {"format": "JSONL"}
url = f"{base_url}{endpoint}"
operators = tdx.get_response(url, params=query)

In [25]:
df = pd.DataFrame(operators)

In [34]:
pd.DataFrame(df["VDLives"][0]["LinkFlows"][0]["Lanes"])

LaneID  LaneType  Speed  Occupancy  \
0       0         1   33.0        2.0   
1       1         1   53.0        4.0   
2       2         1   32.0       30.0   

                                            Vehicles ErrorType  
0  [{'VehicleType': 'M', 'Volume': 0, 'Speed': 0....     diag0  
1  [{'VehicleType': 'S', 'Volume': 7, 'Speed': 55...     diag0  
2  [{'VehicleType': 'L', 'Volume': 5, 'Speed': 17...     diag0

In [87]:
zip(fetch_date["start_date"], fetch_date["end_date"])

## 20230410 Test the historical csv file extract
### For monitoring daily vehicle mileage, just need to keep the columns of:
- *PlateNumb*
- *OperatorID*
- *PositionLon*
- *PositionLat*
- *GeoHash*
- *Speed*
- *UpdateTime*

### Finally only "PlateNumb", "OperatorID", "Distance", "Date" and "AVG. Speed" will be written to database


In [3]:
icb_operator_api = "https://linkmotc.map8.zone/app/data?modelName=operator_coach&skip=0&limit=&whereOptions="
res = httpx.get(icb_operator_api)
df = pd.read_json(res.text)
# df = pd.read_excel(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\國道客運業者名單.xlsx")
operator_cn_dict = dict(zip(df["operator_id"], df["operator_name"]))
operator_en_dict = dict(zip(df["operator_id"], df["operator_name_eng"]))
four = pd.read_excel(r"D:\kc.hsu\OneDrive - Bridgestone\數據\市場資訊\大車監理數據.xlsx", sheet_name="Sheet1")
four["廠牌"] = four["廠牌"].fillna("")
four["車體"] = four["車體"].fillna("")
brand_dict = dict(zip(four["車號"], four["廠牌"]))
body_dict = dict(zip(four["車號"], four["車體"]))

In [2]:
## 建立每月批次整理ICB數據的class
class ICB:
    
    def __init__(self):
        self.run()
        # self.operator_cn_dict, self.operator_en_dict = self.update_operatorID()
        # self.brand_dict, self.body_dict = self.four_color()
    
    def update_operatorID(self):
        icb_operator_api = "https://linkmotc.map8.zone/app/data?modelName=operator_coach&skip=0&limit=&whereOptions="
        res = httpx.get(icb_operator_api)
        df = pd.read_json(res.text)
        operator_cn_dict = dict(zip(df["operator_id"], df["operator_name"]))
        operator_en_dict = dict(zip(df["operator_id"], df["operator_name_eng"]))
        return operator_cn_dict, operator_en_dict
    
    def four_color(self):
        four = pd.read_excel(r"D:\kc.hsu\OneDrive - Bridgestone\數據\市場資訊\大車監理數據.xlsx", sheet_name="Sheet1")
        four["廠牌"] = four["廠牌"].fillna("")
        four["車體"] = four["車體"].fillna("")
        brand_dict = dict(zip(four["車號"], four["廠牌"]))
        body_dict = dict(zip(four["車號"], four["車體"]))
        return brand_dict, body_dict
    
    def select_files(self):
        # 測試讀取檔案路徑list存進txt，看看中斷之後再次讀取是否OK
        root = tk.Tk()
        root.withdraw()
        paths = filedialog.askopenfilenames()

        # 將開啟的路徑都寫進去tdx_path.txt
        with open("tdx_paths.txt", "w", encoding="utf-8") as f:
            for path in paths:
                f.write(path + "\n")
                
                
    def load_files(self):
        if os.path.isfile("./tdx.db"):
            pass
        else:
            self.create_db()
        # 打開tdx_paths.txt並讀取所有路徑
        with open("tdx_paths.txt", "r", encoding="utf-8") as f:
            lines = f.readlines()

        #當路徑list的長度大於0，執行動作，並將路徑從list中刪除，一旦中斷執行，就將剩下還未執行到的路徑list重新寫回檔案中待下次繼續執行
        while len(lines) > 0:
            path = lines[0].rstrip("\n")

            try:
                print("Dealing with {}".format(path))
                df = pd.read_csv(path, usecols=[0,1,12,13,20])
                print("讀取完畢")
                result = self.data_extract(df)
                print("已完成=============" + path.split("/")[-1])
                self.write_db(result)
                print("已將==============={}寫入資料庫".format(path.split("/")[-1]))
                print("移除================{}".format(lines[0].rstrip("\n")))
                lines.pop(0)
                
            
            except Exception as e:
                print(e)
                
            except:
                with open("tdx_paths.txt", "w", encoding="utf-8") as f:
                    for line in lines:
                        f.write(line)
                break
            
            else:
                if len(lines) == 0:
                    os.remove("tdx_paths.txt")
                else:
                    pass
            
            
    def data_extract(self, df):
        data = df.sort_values(by="GPSTime", ascending=True)
        data = data[(data["PlateNumb"] != "???") & (data["PositionLon"].between(-180, 180)) & (data["PositionLat"].between(-85, 85))]
        data["NextGPS"] = data.groupby("PlateNumb")["GPSTime"].shift(-1)
        data["更新時間差"] = pd.to_datetime(data["NextGPS"]) - pd.to_datetime(data["GPSTime"])
        data["更新時間秒差"] = data["更新時間差"].map(lambda x: 0 if pd.isna(x) else x / np.timedelta64(1, "s"))
        data["Coordinates"] = data[["PositionLat", "PositionLon"]].apply(tuple, axis=1)
        data["Land"] = globe.is_land(data["PositionLat"], data["PositionLon"])
        data = data[data["Land"] == True]
        data["NextCoordinates"] = data.groupby("PlateNumb")["Coordinates"].shift(-1)
        data["Distance"] = data.apply(lambda data: geodesic(data["Coordinates"], data["NextCoordinates"]).meters if pd.notna(data["NextCoordinates"]) else 0, axis=1) / 1000
        # data = data[data["Distance"] <= 2.5]
        data["數據有效性"] = data.apply(lambda x: "有效" if  x["Distance"] <= round((130 / 3600) * x["更新時間秒差"], 4) else "無效", axis=1)
        data = data[data["數據有效性"] == "有效"]
        data["Time"] = pd.to_datetime(data["GPSTime"].map(lambda x: x.split("+")[0]), format="%Y-%m-%dT%H:%M")
        result = data.groupby(["PlateNumb", "OperatorID"]).agg({"Distance": "sum", "Time": lambda x: (x.max() - x.min()) / pd.Timedelta(hours=1)}).reset_index()
        result["Date"] = data["Time"].max().strftime("%Y-%m-%d")
        # result["AVG_Speed"] = result["Distance"] / result["Time"]
        # result["AVG_Speed"].fillna(0, inplace=True)
        result[["Distance", "Time"]] = result[["Distance", "Time"]].applymap(lambda x: round(x, 1))
        # result["業者名稱"] = result["OperatorID"].map(self.operator_dict)
        # result["業者中文名稱"] = result["OperatorID"].map(self.operator_cn_dict)
        # result["業者英文名稱"] = result["OperatorID"].map(self.operator_en_dict)
        # result["廠牌"] = result["PlateNumb"].map(self.brand_dict)
        # result["車體"] = result["PlateNumb"].map(self.body_dict)
        result = result[["PlateNumb", "OperatorID", "Distance", "Time", "Date"]]
        return result
    
    def create_db(self):
        # 第一次初始化table才需要執行
        con = sqlite3.connect("./tdx.db")
        cur = con.cursor()

        cur.execute("create table ICB(PlateNumb, OperatorID, Distance, Time, Date)")
        con.commit()
        con.close()
    
    def write_db(self, result):
        con = sqlite3.connect("./tdx.db")
        # cur = con.cursor()
        # for index, row in result.iterrows():
        #     print(tuple(row))
        #     cur.execute('INSERT INTO ICB (PlateNumb, OperatorID_CN, OperatorID_EN, Brand, Model, Distance, Time, Date, AVG_Speed) values (?, ?, ?, ?, ?, ?, ?, ?, ?)', tuple(row))
        result.to_sql('ICB', con, if_exists="append", index=False)
        # del result
        # gc.collect()
        con.commit()
        con.close()
        
        
    def run(self):
        if os.path.isfile("tdx_paths.txt"):
            pass
        else:
            self.select_files()
        self.load_files()
        



In [3]:
icb = ICB()

Dealing with D:/kc.hsu/OneDrive - Bridgestone/數據/TDX/TDX下載/ICB/unzip files/公路客運定時歷史資料(A1)2023-05-16.CSV
讀取完畢
已完成=============公路客運定時歷史資料(A1)2023-05-16.CSV
已將===============公路客運定時歷史資料(A1)2023-05-16.CSV寫入資料庫
移除================D:/kc.hsu/OneDrive - Bridgestone/數據/TDX/TDX下載/ICB/unzip files/公路客運定時歷史資料(A1)2023-05-16.CSV
Dealing with D:/kc.hsu/OneDrive - Bridgestone/數據/TDX/TDX下載/ICB/unzip files/公路客運定時歷史資料(A1)2023-05-17.CSV
讀取完畢
已完成=============公路客運定時歷史資料(A1)2023-05-17.CSV
已將===============公路客運定時歷史資料(A1)2023-05-17.CSV寫入資料庫
移除================D:/kc.hsu/OneDrive - Bridgestone/數據/TDX/TDX下載/ICB/unzip files/公路客運定時歷史資料(A1)2023-05-17.CSV
Dealing with D:/kc.hsu/OneDrive - Bridgestone/數據/TDX/TDX下載/ICB/unzip files/公路客運定時歷史資料(A1)2023-05-18.CSV
讀取完畢
已完成=============公路客運定時歷史資料(A1)2023-05-18.CSV
已將===============公路客運定時歷史資料(A1)2023-05-18.CSV寫入資料庫
移除================D:/kc.hsu/OneDrive - Bridgestone/數據/TDX/TDX下載/ICB/unzip files/公路客運定時歷史資料(A1)2023-05-18.CSV
Dealing with D:/kc.hsu/OneDrive - Bridgestone/數據/TDX/TDX下載

## 數據合併
- 將車輛和營運商的數據合併進每日行駛里程

In [3]:
con = sqlite3.connect("./tdx.db")
icb = pd.read_sql("select * from ICB", con)
icb_info = pd.read_sql("select * from icb_info", con)
operator = pd.read_sql("select * from operator", con)
con.commit()
con.close()

In [23]:
car_info_dict = dict(zip(icb_info["車號"], icb_info[["廠牌", "車體", "動力類型"]].apply(tuple, axis=1)))
operator_dict = dict(zip(operator["operator_id"], operator[["operator_name", "operator_name_eng"]].apply(tuple, axis=1)))

In [24]:
icb["info_tuple"] = icb["PlateNumb"].map(car_info_dict)
icb["operator_tuple"] = icb["OperatorID"].map(operator_dict)

In [37]:
icb[["Brand", "Body", "Power Type"]] = pd.DataFrame(icb["info_tuple"].tolist(), index=icb.index, columns=["Brand", "Body", "Power Type"])

In [39]:
icb[["Operator_name", "Operator_EN_name"]] = pd.DataFrame(icb["operator_tuple"].tolist(), index=icb.index, columns=["Operator_name", "Operator_EN_name"])

In [43]:
result = icb[["PlateNumb", "Operator_name", "Operator_EN_name", "Brand", "Body", "Power Type", "Distance", "Time", "Date"]]

In [49]:
miss_plates = result[result["Brand"].isna()]["PlateNumb"].drop_duplicates().tolist()
with open("missing_plate.txt", "w", encoding="utf-8") as f:
            for miss in miss_plates:
                f.write(miss + "\n")

In [52]:
result["Date"] = pd.to_datetime(result["Date"], format="%Y-%m-%d")

In [54]:
result.to_csv(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\TDX下載\ICB\icb_daily_info.csv", index=False)

## 從api匯入資料

In [2]:
class TDX():
    
    '''
    將常用的屬性放在類別屬性中方便後續呼叫.
    '''
    client_id : str = "kc.hsu-e51d77a0-5d9b-418b"
    client_secret = "afbb6a0a-f69d-4556-bd0b-4e53eae46379"
    cities = ["Taipei", "NewTaipei", "Taoyuan", "Taichung", "Tainan", "Kaohsiung", "Keelung", "Hsinchu", "HsinchuCounty", "MiaoliCounty", "ChanghuaCounty", "NantouCounty", "YunlinCounty", "ChiayiCounty", "ChiayiCounty", "Chiayi", "PingtungCounty", "YilanCounty", "HualienCounty", "TaitungCounty", "KinmenCounty", "PenghuCounty", "LienchiangCounty"]

    
    def __init__(self, client_id=client_id, client_secret=client_secret):
        self.client_id = client_id
        self.client_secret = client_secret
        self.token = self.get_token()
        
    def get_token(self):
        token_url = "https://tdx.transportdata.tw/auth/realms/TDXConnect/protocol/openid-connect/token"
        headers = {'content-type': 'application/x-www-form-urlencoded'}
        data = {
            'grant_type': 'client_credentials',
            'client_id': self.client_id,
            'client_secret': self.client_secret
        }
        response = requests.post(token_url, headers=headers, data=data)
        return response.json()['access_token']
    
    def get_response(self, url, params=None):
        headers = {"authorization": f"Bearer {self.token}"}
        response = requests.get(url, headers=headers, params=params)
        return response.json()
        # return json.loads(response.text)
       

In [24]:
con = sqlite3.connect("./tdx.db")
cur = con.cursor()
max_date_sql = pd.read_sql("select max(Date) as max_date from ICB", con)["max_date"][0]
con.close()

In [29]:
start_date = datetime.datetime.strftime(datetime.datetime.strptime(max_date_sql, "%Y-%m-%d") + timedelta(days=1), "%Y-%m-%d")
latest_date = datetime.datetime.strftime(datetime.datetime.today() + timedelta(days=-1), "%Y-%m-%d")

NameError: name 'max_date_sql' is not defined

In [32]:
tdx = TDX()
base_url = "https://tdx.transportdata.tw/api/historical"
endpoint = "/v2/Historical/Bus/RealTimeByFrequency/InterCity"
date = "Dates={}".format("2023-05-16")
format = "%24format=CSV"
url = base_url + endpoint + "?" + date + "&" + format
print(url)
operators = tdx.get_response(url)
df = pd.DataFrame.from_records(operators)
df

https://tdx.transportdata.tw/api/historical/v2/Historical/Bus/RealTimeByFrequency/InterCity?Dates=2023-05-16&%24format=CSV


JSONDecodeError: Unexpected UTF-8 BOM (decode using utf-8-sig): line 1 column 1 (char 0)

In [24]:
# 抓取國道公車歷史數據
def update_icb_data(start_date, latest_date=None):
    tdx = TDX()
    base_url = "https://tdx.transportdata.tw/api/historical"
    endpoint = "/v2/Historical/Bus/RealTimeByFrequency/InterCity"
    if latest_date == None:
        date = "Dates={}".format(start_date)
    else:
        date = "Dates={}~{}".format(start_date, latest_date)
    format = "%24format=CSV"
    url = base_url + endpoint + "?" + date + "&" + format
    print(url)
    operators = tdx.get_response(url)
    df = pd.DataFrame.from_records(operators)
    return df
    
df = update_icb_data(start_date)

NameError: name 'start_date' is not defined

### 市區公車業者名單抓取

In [11]:
dfs = []
cities = ["Taipei", "NewTaipei", "Taoyuan", "Taichung", "Tainan", "Kaohsiung", "Keelung", "Hsinchu", "HsinchuCounty", "MiaoliCounty", "ChanghuaCounty", "NantouCounty", "YunlinCounty", "ChiayiCounty", "ChiayiCounty", "Chiayi", "PingtungCounty", "YilanCounty", "HualienCounty", "TaitungCounty", "KinmenCounty", "PenghuCounty", "LienchiangCounty"]
for city in cities:
    tdx = TDX()
    base_url = "https://tdx.transportdata.tw/api/basic"
    endpoint = "/v2/Bus/Operator/City/"
    url = f"{base_url}{endpoint}{city}"
    operators = tdx.get_response(url)
    dfs.append(pd.DataFrame.from_records(operators))
df = pd.concat(dfs)
df["OperatorNameZh_tw"] = df["OperatorName"].map(lambda x: x["Zh_tw"])
df.to_excel(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\市區公車業者名單.xlsx", index=False)

### 國道客運業者名單抓取

In [10]:
tdx = TDX()
base_url = "https://tdx.transportdata.tw/api/basic"
endpoint = "/v2/Bus/Operator/InterCity"
url = f"{base_url}{endpoint}"
operators = tdx.get_response(url)
intercity_operators = pd.DataFrame.from_records(operators)
intercity_operators["OperatorNameZh_tw"] = intercity_operators["OperatorName"].map(lambda x: x["Zh_tw"])
intercity_operators.to_excel(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\國道客運業者名單.xlsx", index=False)

## 國道客運即時數據抓取

In [7]:
tdx = TDX()
base_url = "https://tdx.transportdata.tw/api/basic"
endpoint = "/v2/Bus/RealTimeByFrequency/InterCity"
url = base_url + endpoint
result = pd.DataFrame.from_records(tdx.get_response(url))
result = result[['PlateNumb', 'OperatorID', 'RouteUID', 'RouteID',
       'SubRouteUID', 'SubRouteID', 'Direction', 'BusPosition',
       'Speed', 'Azimuth', 'DutyStatus', 'BusStatus', 'MessageType', 'GPSTime',
       'SrcRecTime', 'SrcTransTime', 'UpdateTime']]

In [9]:
result["Longitude"] = result["BusPosition"].map(lambda x: x["PositionLon"])
result["Latitude"] = result["BusPosition"].map(lambda x: x["PositionLat"])

In [11]:
result = result[['PlateNumb', 'OperatorID', 'RouteUID', 'RouteID',
       'SubRouteUID', 'SubRouteID', 'Direction', 'Longitude', 'Latitude',
       'Speed', 'Azimuth', 'DutyStatus', 'BusStatus', 'MessageType', 'GPSTime',
       'SrcRecTime', 'SrcTransTime', 'UpdateTime']]

In [16]:
result["Coordinates"] = result[["Longitude", "Latitude"]].apply(tuple, axis=1)

In [21]:
result.groupby(["OperatorID"])["Coordinates"].shift(-1)

0       (120.786511666667, 24.4588066666667)
1       (121.537478333333, 24.9586483333333)
2       (121.438336666667, 25.0859366666667)
3               (120.298941666667, 23.56911)
4             (120.326695, 22.6297216666667)
                        ...                 
1816                                     NaN
1817            (121.696346666667, 25.15598)
1818                                     NaN
1819    (121.756978333333, 25.1282183333333)
1820                                     NaN
Name: Coordinates, Length: 1821, dtype: object

In [14]:
result.to_excel(r"C:\Users\kc.hsu\Desktop\國道客運API範例內容.xlsx", index=False)

In [ ]:
def time_range_data(st_year=0, st_month=0, st_day=0, st_hour=0, st_min=0, end_year=0, end_month=0, end_day=0, end_hour=0, end_min=0):
    st_time = datetime.datetime(st_year, st_month, st_day, st_hour, st_min).replace(tzinfo=datetime.timezone.utc).astimezone(timezone(timedelta(hours=0))).replace(microsecond=0).isoformat()
    end_time = datetime.datetime(end_year, end_month, end_day, end_hour, end_min).replace(tzinfo=datetime.timezone.utc).astimezone(timezone(timedelta(hours=0))).replace(microsecond=0).isoformat()
    dfs = []
    tdx = TDX()
    while True:
        current_time = datetime.datetime.utcnow().replace(tzinfo=datetime.timezone.utc).astimezone(tz=None).replace(microsecond=0).isoformat()
        if st_time <= current_time <= end_time:
            base_url = "https://tdx.transportdata.tw/api/basic"
            endpoint = "/v2/Bus/RealTimeByFrequency/InterCity" # batch update(Frequency: 60sec.)
            # filter = "Direction eq 1"  # 順逆行: [0:'順行', 1:'逆行']
            url = f"{base_url}{endpoint}"
            try:
                result = pd.DataFrame.from_records(tdx.get_response(url))
            except:
                tdx.token = tdx.get_token()
                continue
            else:
                result["Longitude"] = result["BusPosition"].map(lambda x: x["PositionLon"])
                result["Latitude"] = result["BusPosition"].map(lambda x: x["PositionLat"])
                dfs.append(result)
                time.sleep(60) # Update the data every 60 sec.
        elif current_time < st_time:
            # print("等待開始")
            continue
        else:
            print("抓取結束")
            result = pd.concat(dfs)
            # print(result)
            break
    # result = result[["PlateNumb", "OperatorID", "RouteUID", "Direction", "DutyStatus", "BusStatus", "MessageType", "Latitude", "Longitude", "UpdateTime"]]
    return result
    

In [ ]:
def icb_summary(df):
    direction_dict = {0 : "去程(南下)", 1 : "返程(北上)", 2 : "迴圈(雙向)"}
    busStatus_dict = {0: "正常", 1 : "車禍", 2 : "故障", 3 : "塞車", 4 : "緊急救援", 5 : "加油", 98 : "偏移路線", 99 : "非營業狀態", 100 : "客滿", 101 : "包車出租", 255 : "未知"}
    busDutyStatus_dict = {0: "正常", 1 : "開始", 2 : "結束"}
    operator = pd.read_excel(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\20221026_國道客運業者名單.xlsx")
    operator_dict = dict(zip(operator["OperatorID"].astype(str), operator["OperatorNameZh_tw"]))
    route = pd.read_csv(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\公路客運路線代碼表.csv")
    route_dict = dict(zip(route["路線唯一識別代碼"], route[["起站中文名稱", "終站中文名稱"]].apply(tuple, axis=1)))
    message_dict = {0 : "未知", 1 : "定期", 2 : "非定期"}
    
    df["Land"] = globe.is_land(df["Latitude"], df["Longitude"]) # Verify if the GPS coordinate is bias(Land or Oscean)
    df = df[df["Land"] == True]
    df["Operator"] = df["OperatorID"].astype(str).map(operator_dict)
    df["車輛方向"] = df["Direction"].map(direction_dict)
    df["車輛狀態"] = df["BusStatus"].map(busStatus_dict)
    df["車輛勤務狀態"] = df["DutyStatus"].map(busDutyStatus_dict)
    df["執勤路線"] = df["RouteUID"].map(route_dict)
    df["班車資訊"] = df["MessageType"].map(message_dict)
    
    df["Coordinates"] = df[["Latitude", "Longitude"]].apply(tuple, axis=1)
    df["NextCoordinates"] = df.groupby("PlateNumb")["Coordinates"].shift(-1)
    df["Distance"] = df.apply(lambda df: geodesic(df["Coordinates"], df["NextCoordinates"]).meters if pd.notna(df["NextCoordinates"]) else 0, axis=1) / 1000
    df = df[df["Distance"] <= 2.5]
    df["Time"] = pd.to_datetime(df["UpdateTime"].map(lambda x: x.split("+")[0]), format="%Y-%m-%dT%H:%M")
    
    result = df.groupby(["PlateNumb", "Operator"]).agg({"Distance": "sum", "Time": lambda x: (x.max() - x.min()) / pd.Timedelta(hours=1)}).reset_index()
    result["Date"] = df["Time"].max().strftime("%Y-%m-%d")
    result["AVG. Speed"] = result["Distance"] / result["Time"]
    result["AVG. Speed"].fillna(0, inplace=True)
    
    return result, df

In [ ]:
df = time_range_data(2023, 1, 5, 18, 0, 2023, 1, 5, 18, 1)
# df.to_excel(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\20221028國道客運即時測試數據.xlsx", index=False)

In [ ]:
df

In [ ]:
result, raw = icb_summary(df)

In [ ]:
today = datetime.datetime.today().date().strftime("%Y%m%d")

In [ ]:
path = today + "國道客運即時數據.pkl"

In [ ]:
raw.to_pickle(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\20221109國道客運即時數據.pkl")
result.to_excel(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\20221109國道客運即時匯整數據.xlsx", index=False)

In [ ]:
result = icb_summary(df)
# result.to_excel(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\20221028國道客運即時測試數據_彙整.xlsx", index=False)


## 測試區

In [ ]:
def cb_time_range_data(st_year=0, st_month=0, st_day=0, st_hour=0, st_min=0, end_year=0, end_month=0, end_day=0, end_hour=0, end_min=0):
    cities = ["Taipei", "NewTaipei", "Taoyuan", "Taichung", "Tainan", "Kaohsiung", "Keelung", "Hsinchu", "HsinchuCounty", "MiaoliCounty", "ChanghuaCounty", "NantouCounty", "YunlinCounty", "ChiayiCounty", "ChiayiCounty", "Chiayi", "PingtungCounty", "YilanCounty", "HualienCounty", "TaitungCounty", "KinmenCounty", "PenghuCounty", "LienchiangCounty"]
    city_select = dict()
    for no, city in enumerate(cities):
        print(no, city)
        city_select.setdefault(no, city)
    city = city_select[eval(input("Please type the no. of the city: "))]
    st_time = datetime.datetime(st_year, st_month, st_day, st_hour, st_min).replace(tzinfo=datetime.timezone.utc).astimezone(timezone(timedelta(hours=0))).replace(microsecond=0).isoformat()
    end_time = datetime.datetime(end_year, end_month, end_day, end_hour, end_min).replace(tzinfo=datetime.timezone.utc).astimezone(timezone(timedelta(hours=0))).replace(microsecond=0).isoformat()
    dfs = []
    tdx = TDX()
    while True:
        current_time = datetime.datetime.utcnow().replace(tzinfo=datetime.timezone.utc).astimezone(tz=None).replace(microsecond=0).isoformat()
        if st_time <= current_time <= end_time:
            base_url = "https://tdx.transportdata.tw/api/basic"
            end_point = "/v2/Bus/RealTimeByFrequency/City/{}".format(city) # batch update(Frequency: 60sec.)
            # filter = "Direction eq 1"  # 順逆行: [0:'順行', 1:'逆行']
            url = base_url + end_point
            try:
                result = pd.DataFrame.from_records(tdx.get_response(url))
            except:
                tdx.token = tdx.get_token()
                continue
            else:
                # result["Longitude"] = result["BusPosition"].map(lambda x: x["PositionLon"])
                # result["Latitude"] = result["BusPosition"].map(lambda x: x["PositionLat"])
                dfs.append(result)
                time.sleep(60) # Update the data every 60 sec.
        elif current_time < st_time:
            # print("等待開始")
            continue
        else:
            print("抓取結束")
            result = pd.concat(dfs).reset_index(drop=True)
            # print(result)
            break
    # result = result[["PlateNumb", "OperatorID", "RouteUID", "Direction", "DutyStatus", "BusStatus", "MessageType", "Latitude", "Longitude", "UpdateTime"]]
    return result

In [22]:
cities = ["Taipei", "NewTaipei", "Taoyuan", "Taichung", "Tainan", "Kaohsiung", "Keelung", "Hsinchu", "HsinchuCounty", "MiaoliCounty", "ChanghuaCounty", "NantouCounty", "YunlinCounty", "ChiayiCounty", "ChiayiCounty", "Chiayi", "PingtungCounty", "YilanCounty", "HualienCounty", "TaitungCounty", "KinmenCounty", "PenghuCounty", "LienchiangCounty"]
base_url = "https://tdx.transportdata.tw/api/basic"
end_point = "/v2/Road/Traffic/Live/VD/City/{}"
tdx = TDX()
# dfs = []
# for city in cities:
#     url = base_url + end_point.format(city)
#     try:
#         df = pd.DataFrame.from_records(tdx.get_response(url))
#     except ValueError:
#         pass
#     except:
#         pass
#     else:
#         dfs.append(df)
# df = pd.concat(dfs).reset_index(drop=True)
# print(df)
url = base_url + end_point.format("Taipei")
df = pd.DataFrame.from_records(tdx.get_response(url))
    
    

NameError: name 'TDX' is not defined

In [ ]:
df["VDLives"].apply(pd.Series)["LinkFlows"].apply(pd.Series)

In [ ]:
df["VDLives"].apply(pd.Series)["LinkFlows"].apply(pd.Series)[0].apply(pd.Series)["Lanes"].apply(pd.Series)

In [ ]:
from concurrent.futures import ThreadPoolExecutor

In [ ]:
with ThreadPoolExecutor() as executor:
    tpe = executor.submit(cb_time_range_data, 2022, 11, 17, 15, 11, 2022, 11, 17, 15, 52)
    ntp = executor.submit(cb_time_range_data, 2022, 11, 17, 15, 11, 2022, 11, 17, 15, 52)

In [ ]:
test_data = cb_time_range_data(2022, 11, 17, 15, 11, 2022, 11, 17, 15, 40)

In [ ]:
test = test_data.reset_index(drop=True)

In [ ]:
test[(test["OperatorID"] == "100") & (test["PlateNumb"].isin(["KKA-1225", "KKA-1232"]))]

In [ ]:
direction_dict = {0 : "去程(南下)", 1 : "返程(北上)", 2 : "迴圈(雙向)"}
busStatus_dict = {0: "正常", 1 : "車禍", 2 : "故障", 3 : "塞車", 4 : "緊急救援", 5 : "加油", 98 : "偏移路線", 99 : "非營業狀態", 100 : "客滿", 101 : "包車出租", 255 : "未知"}
busDutyStatus_dict = {0: "正常", 1 : "開始", 2 : "結束"}
operator = pd.read_excel(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\20221026_國道客運業者名單.xlsx")
operator_dict = dict(zip(operator["OperatorID"], operator["OperatorNameZh_tw"]))
route = pd.read_csv(r"D:\kc.hsu\OneDrive - Bridgestone\數據\TDX\公路客運路線代碼表.csv")
route_dict = dict(zip(route["路線唯一識別代碼"], route[["起站中文名稱", "終站中文名稱"]].apply(tuple, axis=1)))
message_dict = {0 : "未知", 1 : "定期", 2 : "非定期"}
df["Operator"] = df["OperatorID"].map(operator_dict)
df["車輛方向"] = df["Direction"].map(direction_dict)
df["車輛狀態"] = df["BusStatus"].map(busStatus_dict)
df["車輛勤務狀態"] = df["DutyStatus"].map(busDutyStatus_dict)
df["執勤路線"] = df["RouteUID"].map(route_dict)
df["班車資訊"] = df["MessageType"].map(message_dict)